# February 21, 2020

## PLANNING IN THE REAL WORLD
---
## PROBLEM
The `Problem` class is a wrapper for `PlanningProblem` with some additional functionality and data-structures to handle real-world planning problems that involve time and resource constraints.
The `Problem` class includes everything that the `PlanningProblem` class includes.
Additionally, it also includes the following attributes essential to define a real-world planning problem:
- a list of `jobs` to be done
- a dictionary of `resources`

It also overloads the `act` method to call the `do_action` method of the `HLA` class, 
and also includes a new method `refinements` that finds refinements or primitive actions for high level actions.
<br>
`hierarchical_search` and `angelic_search` are also built into the `Problem` class to solve such planning problems.

In [28]:
from planningv2 import *
from notebook import psource

In [29]:
psource(Problem)

## HLA = High-Level Action
To be able to model a real-world planning problem properly, it is  essential to be able to represent a _high-level action (HLA)_ that can be hierarchically reduced to primitive actions.

Note: I have modified planningv2.py to include the debug decorator for HLA do_action

In [30]:
psource(debug)

In [31]:
psource(HLA)

In addition to preconditions and effects, an object of the `HLA` class also stores:
- the `duration` of the HLA
- the quantity of consumption of _consumable_ resources
- the quantity of _reusable_ resources used
- a bool `completed` denoting if the `HLA` has been completed

The class also has some useful helper methods:
- `do_action`: checks if required consumable and reusable resources are available and if so, executes the action.
- `has_consumable_resource`: checks if there exists sufficient quantity of the required consumable resource.
- `has_usable_resource`: checks if reusable resources are available and not already engaged.
- `inorder`: ensures that all the jobs that had to be executed before the current one have been successfully executed.

## PLANNING PROBLEMS
---
## Job-shop Problem
This is a simple problem involving the assembly of two cars simultaneously.
The problem consists of two jobs, each of the form [`AddEngine`, `AddWheels`, `Inspect`] to be performed on two cars with different requirements and availability of resources.
<br>
Let's look at how the `job_shop_problem` has been defined on the  module.

In [32]:
psource(job_shop_problem)

The states of this problem are:
<br>
<br>
**Has(x, y)**: Car **'x'** _has_ **'y'** where **'y'** can be an Engine or a Wheel.

**~Has(x, y)**: Car **'x'** does _not have_ **'y'** where **'y'** can be an Engine or a Wheel.

**Inspected(c)**: Car **'c'** has been _inspected_.

**~Inspected(c)**: Car **'c'** has _not_ been inspected.

In the initial state, `C1` and `C2` are cars and neither have an engine or wheels and haven't been inspected.
`E1` and `E2` are engines.
`W1` and `W2` are wheels.
<br>
Our goal is to have engines and wheels on both cars and to get them inspected. We will discuss how to achieve this.
<br>
Let's define an object of the `job_shop_problem`.

In [33]:
jobShopProblem = job_shop_problem()

Before taking any actions, we will check if `jobShopProblem` has reached its goal.

In [34]:
print(jobShopProblem.goal_test())

False


We now define a possible solution that can help us reach the goal. 
The actions are then carried out on the `jobShopProblem` object.

The following actions are available to us:

**AddEngine1**: Adds an engine to the car C1. Takes 30 minutes to complete and uses an engine hoist.
 
**AddEngine2**: Adds an engine to the car C2. Takes 60 minutes to complete and uses an engine hoist.

**AddWheels1**: Adds wheels to car C1. Takes 30 minutes to complete. Uses a wheel station and consumes 20 lug nuts.

**AddWheels2**: Adds wheels to car C2. Takes 15 minutes to complete. Uses a wheel station and consumes 20 lug nuts as well.

**Inspect1**: Gets car C1 inspected. Requires 10 minutes of inspection by one inspector.

**Inspect2**: Gets car C2 inspected. Requires 10 minutes of inspection by one inspector.

In [35]:
solution = [jobShopProblem.jobs[1][0],
            jobShopProblem.jobs[1][1],
            jobShopProblem.jobs[1][2],
            jobShopProblem.jobs[0][0],
            jobShopProblem.jobs[0][1],
            jobShopProblem.jobs[0][2]]

for action in solution:
    jobShopProblem.act(action)

Calling: do_action with args: (HLA(AddEngine2), [[HLA(AddEngine1), HLA(AddWheels1), HLA(Inspect1)], [HLA(AddEngine2), HLA(AddWheels2), HLA(Inspect2)]], {'EngineHoists': 1, 'WheelStations': 2, 'Inspectors': 2, 'LugNuts': 500}, [Car(C1), Car(C2), Wheels(W1), Wheels(W2), Engine(E2), Engine(E2), NotHas(C1, E1), NotHas(C2, E2), NotHas(C1, W1), NotHas(C2, W2), NotInspected(C1), NotInspected(C2)], ())
Exiting: do_action with value: <logic.FolKB object at 0x7f012bcdef90>

Calling: do_action with args: (HLA(AddWheels2), [[HLA(AddEngine1), HLA(AddWheels1), HLA(Inspect1)], [HLA(AddEngine2), HLA(AddWheels2), HLA(Inspect2)]], {'EngineHoists': 1, 'WheelStations': 2, 'Inspectors': 2, 'LugNuts': 500}, [Car(C1), Car(C2), Wheels(W1), Wheels(W2), Engine(E2), Engine(E2), NotHas(C1, E1), NotHas(C1, W1), NotHas(C2, W2), NotInspected(C1), NotInspected(C2), Has(C2, E2)], ())
Exiting: do_action with value: <logic.FolKB object at 0x7f012bd0a350>

Calling: do_action with args: (HLA(Inspect2), [[HLA(AddEngine1), 

The above output is due to the debug decorator.  If you remove debug, there is no output.

In [36]:
print(jobShopProblem.goal_test())

True


This is a valid solution and one of many correct ways to solve this problem.

In [37]:
jobShopProblem.resources

{'EngineHoists': 1, 'WheelStations': 2, 'Inspectors': 2, 'LugNuts': 460}

## Double tennis problem
This problem is a simple case of a multiactor planning problem, where two agents act at once and can simultaneously change the current state of the problem. 
A correct plan is one that, if executed by the actors, achieves the goal.
In the true multiagent setting, of course, the agents may not agree to execute any particular plan, but atleast they will know what plans _would_ work if they _did_ agree to execute them.
<br>
In the double tennis problem, two actors A and B are playing together and can be in one of four locations: `LeftBaseLine`, `RightBaseLine`, `LeftNet` and `RightNet`.
The ball can be returned only if a player is in the right place.
Each action must include the actor as an argument.
<br>
Let's first look at the definition of the `double_tennis_problem` in the module.

In [38]:
psource(double_tennis_problem)

The states of this problem are:

**Approaching(Ball, loc)**: The `Ball` is approaching the location `loc`.

**Returned(Ball)**: One of the actors successfully hit the approaching ball from the correct location which caused it to return to the other side.

**At(actor, loc)**: `actor` is at location `loc`.

**~At(actor, loc)**: `actor` is _not_ at location `loc`.

Let's now define an object of `double_tennis_problem`.


In [39]:
doubleTennisProblem = double_tennis_problem()

Before taking any actions, we will check if `doubleTennisProblem` has reached the goal.

In [40]:
print(doubleTennisProblem.goal_test())

False


As we can see, the goal hasn't been reached. 
We now define a possible solution that can help us reach the goal of having the ball returned.
The actions will then be carried out on the `doubleTennisProblem` object.

The actions available to us are the following:

**Hit(actor, ball, loc)**: returns an approaching ball if `actor` is present at the `loc` that the ball is approaching.

**Go(actor, to, loc)**: moves an `actor` from location `loc` to location `to`.

We notice something different in this problem though, 
which is quite unlike any other problem we have seen so far. 
The goal state of the problem contains a variable `a`.
This happens sometimes in multiagent planning problems 
and it means that it doesn't matter _which_ actor is at the `LeftNet` or the `RightNet`, as long as there is atleast one actor at either `LeftNet` or `RightNet`.

In [41]:
solution = [expr('Go(A, RightBaseLine, LeftBaseLine)'),
            expr('Hit(A, Ball, RightBaseLine)'),
            expr('Go(A, LeftNet, RightBaseLine)')]

for action in solution:
    doubleTennisProblem.act(action)

In [44]:
doubleTennisProblem.goal_test()

False

Oops!  It did not work!  There is a bug in the code.  Find the bug and report it in polleverywhere.

In [43]:
dir(doubleTennisProblem)

['__class__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__le__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__setattr__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 'act',
 'actions',
 'convert',
 'goal_test',
 'goals',
 'init']

In [27]:
doubleTennisProblem.goals

[Returned(Ball), At(A, LeftNet), At(A, RightNet)]

In [19]:
doubleTennisProblem.init

[At(B, RightNet),
 Approaching(Ball, RightBaseLine),
 Partner(A, B),
 Partner(B, A),
 NotAt(A, LeftBaseLine),
 Returned(Ball),
 At(A, LeftNet),
 NotAt(A, RightBaseLine)]